In [ ]:
import pandas as pd
import numpy as np

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
movie_plots_path = "/content/drive/MyDrive/NLP/American_movie_plots_2005_2021_v1.csv"

In [ ]:
df = pd.read_csv(movie_plots_path)
print (df.shape)
df.head()

(3503, 4)


Unnamed: 0                        Movie Name  \
0           0                       White Noise   
1           1                      Coach Carter   
2           2                           Elektra   
3           3                    Racing Stripes   
4           4  Tom and Jerry: Blast Off to Mars   

                                           Wiki link  \
0  https://en.wikipedia.org/wiki/White_Noise_(200...   
1         https://en.wikipedia.org/wiki/Coach_Carter   
2  https://en.wikipedia.org/wiki/Elektra_(2005_film)   
3       https://en.wikipedia.org/wiki/Racing_Stripes   
4  https://en.wikipedia.org/wiki/Tom_and_Jerry:_B...   

                                                Plot  
0  Jonathan Rivers is an architect, married to hi...  
1  In Richmond, California, Ken Carter becomes th...  
2  After being killed,[a] Elektra Natchios is rev...  
3  During a thunderstorm, a traveling circus, Cir...  
4  Tom chases Jerry as usual from their house and...

In [ ]:
print (df.shape)
df.drop_duplicates(subset ="Wiki link", keep = False, inplace = True)
print (df.shape)

(3503, 4)
(3483, 4)


In [ ]:
movie_df  = df[df['Movie Name'].str.match('Interstellar')]
movie_plot = movie_df.iloc[0]['Plot']
print (movie_plot)

In 2067, humanity is facing extinction following a global famine caused by ecocide.[7] Joseph Cooper, a former NASA test pilot, along with his son and daughter, Tom and Murph, and father-in-law Donald, are farmers, like most of humanity. One evening, during a dust storm, Cooper and Murph discover a gravitational anomaly in Murph's bedroom that has left patterns of falling particles. The pattern leads them to a secret NASA facility, where Cooper gets enlisted by the lead scientist, Brand, as the pilot of their latest mission, which will take them beyond the galaxy in search of new habitable planets. This can now be achieved via a mysterious wormhole − another anomaly − near Saturn, leading to a faraway planetary system orbiting Gargantua, a supermassive black hole. 

Cooper struggles to leave his children behind, but decides to do it in the hope of saving Tom and Murph's generation from extinction. He promises Murph to return, but she is distraught. Cooper joins the Endurance team, cons

### extracting keywords

In [ ]:
!python3 -m spacy download en_core_web_md

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.8/42.8 MB 18.2 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_md')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


In [ ]:
import spacy
nlp = spacy.load('en_core_web_md')


def get_noun_phrases(sample_text):
  candidates =[]
  doc = nlp(sample_text)
  for np in doc.noun_chunks:
    phrase = np.text
    # no_of_words = phrase.split()
    # if len(no_of_words)>=2 and len(no_of_words)<=4:
    #   phrase = np.text
    phrase = phrase.strip()
    if phrase not in candidates:
      candidates.append(phrase)
  return candidates

print (get_noun_phrases(movie_plot))

['humanity', 'extinction', 'a global famine', 'Joseph Cooper', 'a former NASA test pilot', 'his son', 'daughter', 'Tom', 'Murph', 'law', 'farmers', 'a dust storm', 'Cooper', 'a gravitational anomaly', "Murph's bedroom", 'that', 'patterns', 'falling particles', 'The pattern', 'them', 'a secret NASA facility', 'the lead scientist', 'Brand', 'the pilot', 'their latest mission', 'which', 'the galaxy', 'search', 'new habitable planets', 'This', 'a mysterious wormhole', 'another anomaly', '−', 'Saturn', 'a faraway planetary system', 'Gargantua', 'a supermassive black hole', 'his children', 'it', 'the hope', "Tom and Murph's generation", 'He', 'she', 'the Endurance team', 'Romilly', 'Doyle', "Brand's daughter", 'Amelia', 'two intelligent robots', 'TARS', 'CASE', 'years', 'travel', 'the crew', 'the wormhole', 'the first candidate planet', 'the new galaxy', 'an ocean world', 'massive tidal waves', "Gargantua's intense gravitational pull", 'a wave', 'the Endurance', 'time dilation', '23 years', 

In [ ]:
np_movie = get_noun_phrases(movie_plot)
print (np_movie)

['humanity', 'extinction', 'a global famine', 'Joseph Cooper', 'a former NASA test pilot', 'his son', 'daughter', 'Tom', 'Murph', 'law', 'farmers', 'a dust storm', 'Cooper', 'a gravitational anomaly', "Murph's bedroom", 'that', 'patterns', 'falling particles', 'The pattern', 'them', 'a secret NASA facility', 'the lead scientist', 'Brand', 'the pilot', 'their latest mission', 'which', 'the galaxy', 'search', 'new habitable planets', 'This', 'a mysterious wormhole', 'another anomaly', '−', 'Saturn', 'a faraway planetary system', 'Gargantua', 'a supermassive black hole', 'his children', 'it', 'the hope', "Tom and Murph's generation", 'He', 'she', 'the Endurance team', 'Romilly', 'Doyle', "Brand's daughter", 'Amelia', 'two intelligent robots', 'TARS', 'CASE', 'years', 'travel', 'the crew', 'the wormhole', 'the first candidate planet', 'the new galaxy', 'an ocean world', 'massive tidal waves', "Gargantua's intense gravitational pull", 'a wave', 'the Endurance', 'time dilation', '23 years', 

In [ ]:
print (len(np_movie))

147


In [ ]:
!pip install --upgrade sentence-transformers
!pip install --upgrade huggingface-hub

In [ ]:
from sentence_transformers import SentenceTransformer

# Initialize the model
model = SentenceTransformer('all-MiniLM-L12-v2')

# Define the function to get document and candidate embeddings
def get_doc_and_candidate_embeddings(transformermodel, doc_text, candidate_phrases):
    doc_embedding = transformermodel.encode([doc_text])
    candidate_embeddings = transformermodel.encode(candidate_phrases)
    return doc_embedding, candidate_embeddings

# Example usage
doc_text = "This is a sample document."
candidate_phrases = ["This is a candidate phrase.", "Another candidate phrase."]
doc_embedding, candidate_embeddings = get_doc_and_candidate_embeddings(model, doc_text, candidate_phrases)

print("Document Embedding:", doc_embedding)
print("Candidate Embeddings:", candidate_embeddings)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Document Embedding: [[-3.02025564e-02  1.12676017e-01 -5.05581386e-02  3.21350321e-02
   4.95909490e-02  3.73795889e-02 -1.03133641e-01  2.37957444e-02
  -5.99682555e-02 -2.56484584e-03  6.98363185e-02 -2.84443162e-02
   3.44656445e-02 -6.11039475e-02 -1.19375385e-01 -4.72530024e-03
   7.18518570e-02  1.81390792e-02  6.45975545e-02  1.12382606e-01
   6.98619634e-02 -1.69988181e-02  6.12231269e-02 -3.61582115e-02
   4.34921309e-03 -2.25573201e-02 -1.76461898e-02  1.95444301e-02
   4.52723354e-02 -5.77725321e-02  2.44170949e-02  9.99302492e-02
   7.85316527e-02  5.71146198e-02 -2.41448265e-02  3.15932222e-02
   1.01223819e-01  2.35750806e-02  2.66588223e-03  5.96333146e-02
   4.09346074e-02 -2.91515682e-02 -3.15061100e-02  8.64383206e-02
  -7.24800229e-02 -3.55006307e-02 -2.89575709e-03  3.66606959e-03
  -2.41758302e-02 -1.81958396e-02 -5.24050295e-02 -9.06459391e-02
  -4.57872115e-02  2.38153134e-02 -1.57142244e-02 -4.59081680e-02
   8.83961655e-03  4.70207222e-02 -2.96337400e-02 -2.383

In [ ]:
document_embedd, keyphrase_embedds = get_doc_and_candidate_embeddings(model,movie_plot,np_movie)

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

# Extract similarity within words, and between words and the document
word_doc_similarity = cosine_similarity(keyphrase_embedds, document_embedd)
word_doc_similarity = word_doc_similarity.flatten()
# print (word_doc_similarity)
print (word_doc_similarity.flatten())
print (word_doc_similarity.shape)

keywords_idx = np.argsort(word_doc_similarity)
keywords_idx = keywords_idx[::-1]

print (word_doc_similarity[keywords_idx])

[0.3714002  0.4070992  0.3641065  0.4308083  0.54438365 0.1697841
 0.13519944 0.20715173 0.26081902 0.05210584 0.22665307 0.23436296
 0.423599   0.3502645  0.22937381 0.13455042 0.13220039 0.28710508
 0.1792221  0.15584634 0.42278004 0.40932697 0.17839438 0.4170936
 0.32066208 0.10925922 0.33043683 0.13294558 0.26145104 0.11463572
 0.3197087  0.17780001 0.14351279 0.23572315 0.2960655  0.19072708
 0.19545382 0.19490921 0.12522127 0.18455607 0.304525   0.14051168
 0.05686707 0.20273808 0.18295696 0.14925145 0.25239888 0.22940916
 0.16308542 0.03693851 0.1391254  0.08961461 0.25008354 0.40394804
 0.34712905 0.3039663  0.3748075  0.19359633 0.18945667 0.23173249
 0.11500641 0.1862558  0.18781315 0.10396455 0.28580755 0.22883795
 0.24723321 0.1671541  0.2926678  0.14203136 0.28074914 0.14618893
 0.09080522 0.07321323 0.24228491 0.10358298 0.24689785 0.30208987
 0.0780239  0.05686707 0.16108036 0.08763468 0.0507795  0.19068766
 0.3021294  0.34052658 0.18562755 0.14975739 0.22669533 0.464296

In [ ]:
sorted_keywords =[]


for index in keywords_idx:
  sorted_keywords.append(np_movie[index])


print (sorted_keywords)

['a former NASA test pilot', 'the surviving NASA explorer', 'the damaged spacecraft', 'Joseph Cooper', 'Cooper', 'a secret NASA facility', 'the pilot', 'the lead scientist', 'extinction', 'the crew', 'the new galaxy', 'humanity', 'a global famine', 'another solo mission', 'the final planet', 'ejecting Cooper', 'a gravitational anomaly', 'the wormhole', 'the Endurance crew', "Cooper's wristwatch", 'the third and final planet', 'the galaxy', 'the new habitable world', 'the NASA coordinates', 'their latest mission', 'a mysterious wormhole', 'a spacecraft', 'the black hole', "Amelia's mass-reduced craft", 'gravity', 'this mission', "Tom and Murph's generation", 'the final candidate planet', 'the first candidate planet', 'the second candidate planet', 'their eventual doom', 'humankind', 'a faraway planetary system', 'the planet', 'his perennially unsolved gravity manipulation equation', 'falling particles', 'Earth', 'potentially habitable worlds', 'the singularity', 'new habitable planets',

### maximum marginal relevance

In [ ]:
from typing import List, Tuple
import itertools
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

def mmr(doc_embedding: np.ndarray,
        word_embeddings: np.ndarray,
        words: List[str],
        top_n: int = 6,
        diversity: float = 0.95) -> List[Tuple[str, float]]:
    """ Calculate Maximal Marginal Relevance (MMR)
    between candidate keywords and the document.


    MMR considers the similarity of keywords/keyphrases with the
    document, along with the similarity of already selected
    keywords and keyphrases. This results in a selection of keywords
    that maximize their within diversity with respect to the document.

    Arguments:
        doc_embedding: The document embeddings
        word_embeddings: The embeddings of the selected candidate keywords/phrases
        words: The selected candidate keywords/keyphrases
        top_n: The number of keywords/keyhprases to return
        diversity: How diverse the select keywords/keyphrases are.
                   Values between 0 and 1 with 0 being not diverse at all
                   and 1 being most diverse.

    Returns:
         List[Tuple[str, float]]: The selected keywords/keyphrases with their distances

    """

    # Extract similarity within words, and between words and the document
    word_doc_similarity = cosine_similarity(word_embeddings, doc_embedding)
    word_similarity = cosine_similarity(word_embeddings)

    # Initialize candidates and already choose best keyword/keyphras
    keywords_idx = [np.argmax(word_doc_similarity)]
    candidates_idx = [i for i in range(len(words)) if i != keywords_idx[0]]

    for _ in range(top_n - 1):
        # Extract similarities within candidates and
        # between candidates and selected keywords/phrases
        candidate_similarities = word_doc_similarity[candidates_idx, :]
        target_similarities = np.max(word_similarity[candidates_idx][:, keywords_idx], axis=1)

        # Calculate MMR
        mmr = (1-diversity) * candidate_similarities - diversity * target_similarities.reshape(-1, 1)
        mmr_idx = candidates_idx[np.argmax(mmr)]

        # Update keywords & candidates
        keywords_idx.append(mmr_idx)
        candidates_idx.remove(mmr_idx)

    return [(words[idx], round(float(word_doc_similarity.reshape(1, -1)[0][idx]), 4)) for idx in keywords_idx]

In [ ]:
final_distractors = mmr(document_embedd,keyphrase_embedds,np_movie,5)
print (final_distractors)

[('a former NASA test pilot', 0.5444), ('The tesseract dissolves', 0.187), ('two intelligent robots', 0.1631), ('returns', 0.0876), ('a global famine', 0.3641)]


In [ ]:
final_distractors = mmr(document_embedd,keyphrase_embedds,np_movie,5,diversity=0.25)
print (final_distractors)

[('a former NASA test pilot', 0.5444), ('extinction', 0.4071), ('Cooper', 0.4236), ('the damaged spacecraft', 0.4394), ('the crew', 0.4039)]


In [ ]:
from typing import List, Tuple
import itertools
def max_sum_similarity(doc_embedding: np.ndarray,
                       word_embeddings: np.ndarray,
                       words: List[str],
                       top_n: int,
                       nr_candidates: int) -> List[Tuple[str, float]]:
    """ Calculate Max Sum Distance for extraction of keywords
    We take the 2 x top_n most similar words/phrases to the document.
    Then, we take all top_n combinations from the 2 x top_n words and
    extract the combination that are the least similar to each other
    by cosine similarity.
    NOTE:
        This is O(n^2) and therefore not advised if you use a large top_n
    Arguments:
        doc_embedding: The document embeddings
        word_embeddings: The embeddings of the selected candidate keywords/phrases
        words: The selected candidate keywords/keyphrases
        top_n: The number of keywords/keyhprases to return
        nr_candidates: The number of candidates to consider
    Returns:
         List[Tuple[str, float]]: The selected keywords/keyphrases with their distances
    """
    if nr_candidates < top_n:
        raise Exception("Make sure that the number of candidates exceeds the number "
                        "of keywords to return.")

    # Calculate distances and extract keywords
    distances = cosine_similarity(doc_embedding, word_embeddings)
    distances_words = cosine_similarity(word_embeddings, word_embeddings)

    # Get 2*top_n words as candidates based on cosine similarity
    words_idx = list(distances.argsort()[0][-nr_candidates:])
    words_vals = [words[index] for index in words_idx]
    candidates = distances_words[np.ix_(words_idx, words_idx)]

    # Calculate the combination of words that are the least similar to each other
    min_sim = 100_000
    candidate = None
    for combination in itertools.combinations(range(len(words_idx)), top_n):
        sim = sum([candidates[i][j] for i in combination for j in combination if i != j])
        if sim < min_sim:
            candidate = combination
            min_sim = sim

    return [(words_vals[idx], round(float(distances[0][idx]), 4)) for idx in candidate]

In [ ]:
print ( max_sum_similarity(document_embedd,keyphrase_embedds,np_movie,6,20))

[("Cooper's wristwatch", 0.3714), ('a gravitational anomaly', 0.4308), ('ejecting Cooper', 0.5444), ('a global famine', 0.2072), ('the crew', 0.2267), ('the surviving NASA explorer', 0.1792)]


### find similar documents

In [ ]:
df.head()

Unnamed: 0                        Movie Name  \
0           0                       White Noise   
1           1                      Coach Carter   
2           2                           Elektra   
3           3                    Racing Stripes   
4           4  Tom and Jerry: Blast Off to Mars   

                                           Wiki link  \
0  https://en.wikipedia.org/wiki/White_Noise_(200...   
1         https://en.wikipedia.org/wiki/Coach_Carter   
2  https://en.wikipedia.org/wiki/Elektra_(2005_film)   
3       https://en.wikipedia.org/wiki/Racing_Stripes   
4  https://en.wikipedia.org/wiki/Tom_and_Jerry:_B...   

                                                Plot  
0  Jonathan Rivers is an architect, married to hi...  
1  In Richmond, California, Ken Carter becomes th...  
2  After being killed,[a] Elektra Natchios is rev...  
3  During a thunderstorm, a traveling circus, Cir...  
4  Tom chases Jerry as usual from their house and...

In [ ]:
all_plots = df['Plot'].tolist()
print (len(all_plots))

3483


In [ ]:
batmanbegins_df  = df[df['Movie Name'].str.match('Batman Begins')]
batmanbegins_plot = batmanbegins_df.iloc[0]['Plot']
print (batmanbegins_plot)

In Gotham City, after falling down a well and getting swarmed by bats, a young Bruce Wayne develops a fear of them. At the opera with his parents, Bruce becomes unsettled by performers masquerading as bats and asks to leave. Outside, mugger Joe Chill murders Bruce's parents in front of him. Bruce is raised by the family butler, Alfred Pennyworth.

Fourteen years later, Chill testifies against the mafia crime boss, Carmine Falcone, and is paroled. Bruce intends to murder Chill to avenge his parents, but one of Falcone's hitmen does so first. Bruce's childhood friend, Rachel Dawes, berates him for acting outside the justice system. After confronting Falcone, who says real power comes from being feared, Bruce spends the next seven years traveling the world, training in combat, and immersing himself in the criminal underworld.

In a Bhutan prison, he is approached by Henri Ducard, who recruits him to the League of Shadows, led by Ra's al Ghul. The League believes Gotham is beyond saving an

In [ ]:
document_embedd, plot_embedds = get_doc_and_candidate_embeddings(model,batmanbegins_plot,all_plots)

In [ ]:
word_doc_similarity = cosine_similarity(plot_embedds, document_embedd)
word_doc_similarity = word_doc_similarity.flatten()

plots_idx = np.argsort(word_doc_similarity)
plots_idx = plots_idx[::-1]

sorted_plots =[]
sorted_titles=[]

all_titles=df['Movie Name'].tolist()

for index in plots_idx:
  sorted_plots.append(all_plots[index])
  sorted_titles.append(all_titles[index])


N = 6

for plot,title in zip(sorted_plots[:N],sorted_titles[:N]):
  print (title)
  print (plot)
  print ("\n\n")

Batman Begins
In Gotham City, after falling down a well and getting swarmed by bats, a young Bruce Wayne develops a fear of them. At the opera with his parents, Bruce becomes unsettled by performers masquerading as bats and asks to leave. Outside, mugger Joe Chill murders Bruce's parents in front of him. Bruce is raised by the family butler, Alfred Pennyworth.

Fourteen years later, Chill testifies against the mafia crime boss, Carmine Falcone, and is paroled. Bruce intends to murder Chill to avenge his parents, but one of Falcone's hitmen does so first. Bruce's childhood friend, Rachel Dawes, berates him for acting outside the justice system. After confronting Falcone, who says real power comes from being feared, Bruce spends the next seven years traveling the world, training in combat, and immersing himself in the criminal underworld.

In a Bhutan prison, he is approached by Henri Ducard, who recruits him to the League of Shadows, led by Ra's al Ghul. The League believes Gotham is be

### precompute embeddings and store them as csv

In [ ]:
from sentence_transformers import SentenceTransformer
model= SentenceTransformer('all-MiniLM-L12-v2')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [ ]:
movie_plots = df['Plot'].tolist()
print (len(movie_plots))
print (movie_plots[0])

3483
Jonathan Rivers is an architect, married to his wife Anna, a best-selling author. The couple have a young son from Jonathan's previous marriage, and Anna is newly pregnant. One evening, Anna fails to arrive home and becomes missing for five weeks without explanation.

Soon after Anna's disappearance, Jonathan is contacted by Raymond Price, whose son has died. Raymond explains he has received frequent communication from his son and other spirits via electronic voice phenomena (EVP), claiming to also have recorded voice messages from Anna and suggests she is dead. Jonathan is initially dismissive and angered, yet he later learns of his wife's tragic drowning. The news reports the incident as an accidental death. 

Jonathan encounters numerous instances of what he interprets as Anna attempting to contact him. Desperate, he visits Raymond to inquire more on EVP. During this visit, Jonathan is befriended by Sarah Tate, a woman who has also come to Raymond for his EVP work because her f

In [ ]:
embeddings = model.encode(movie_plots,show_progress_bar=True)

Batches:   0%|          | 0/109 [00:00<?, ?it/s]

In [ ]:
df['full_embeddings']= embeddings.tolist()
df.head()

Unnamed: 0                        Movie Name  \
0           0                       White Noise   
1           1                      Coach Carter   
2           2                           Elektra   
3           3                    Racing Stripes   
4           4  Tom and Jerry: Blast Off to Mars   

                                           Wiki link  \
0  https://en.wikipedia.org/wiki/White_Noise_(200...   
1         https://en.wikipedia.org/wiki/Coach_Carter   
2  https://en.wikipedia.org/wiki/Elektra_(2005_film)   
3       https://en.wikipedia.org/wiki/Racing_Stripes   
4  https://en.wikipedia.org/wiki/Tom_and_Jerry:_B...   

                                                Plot  \
0  Jonathan Rivers is an architect, married to hi...   
1  In Richmond, California, Ken Carter becomes th...   
2  After being killed,[a] Elektra Natchios is rev...   
3  During a thunderstorm, a traveling circus, Cir...   
4  Tom chases Jerry as usual from their house and...   

                                     full_embeddings  
0  [-0.03315874934196472, 0.07238175719976425, 0....  
1  [-0.05740576982498169, 0.04432478919625282, 0....  
2  [-0.048524562269449234, 0.022518325597047806, ...  
3  [-0.02799609676003456, 0.053856637328863144, -...  
4  [0.036791738122701645, 0.08663170784711838, 0....

In [ ]:
movie_plots_with_embeddings = "/content/drive/MyDrive/NLP/American_movie_plots_2005_2021_v1_embeddings.csv"

In [ ]:
df.to_csv(movie_plots_with_embeddings,index=False)

# Topic Modelling using BERTopic

In [ ]:
movie_plots_path = "/content/drive/MyDrive/NLP/American_movie_plots_2005_2021_v1_embeddings.csv"

In [ ]:
import pandas as pd
import ast
df = pd.read_csv(movie_plots_path,converters={'full_embeddings':ast.literal_eval})
print (df.shape)
df.head()

(3483, 5)


Unnamed: 0                        Movie Name  \
0           0                       White Noise   
1           1                      Coach Carter   
2           2                           Elektra   
3           3                    Racing Stripes   
4           4  Tom and Jerry: Blast Off to Mars   

                                           Wiki link  \
0  https://en.wikipedia.org/wiki/White_Noise_(200...   
1         https://en.wikipedia.org/wiki/Coach_Carter   
2  https://en.wikipedia.org/wiki/Elektra_(2005_film)   
3       https://en.wikipedia.org/wiki/Racing_Stripes   
4  https://en.wikipedia.org/wiki/Tom_and_Jerry:_B...   

                                                Plot  \
0  Jonathan Rivers is an architect, married to hi...   
1  In Richmond, California, Ken Carter becomes th...   
2  After being killed,[a] Elektra Natchios is rev...   
3  During a thunderstorm, a traveling circus, Cir...   
4  Tom chases Jerry as usual from their house and...   

                                     full_embeddings  
0  [-0.03315874934196472, 0.07238175719976425, 0....  
1  [-0.05740576982498169, 0.04432478919625282, 0....  
2  [-0.048524562269449234, 0.022518325597047806, ...  
3  [-0.02799609676003456, 0.053856637328863144, -...  
4  [0.036791738122701645, 0.08663170784711838, 0....

In [ ]:
!pip install --upgrade textwrap3
!pip install --upgrade umap-learn
!pip install --upgrade hdbscan
!pip install --upgrade pyyaml

  Using cached hdbscan-0.8.36-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.6 MB)
  Using cached Cython-0.29.37-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.manylinux_2_24_x86_64.whl (1.9 MB)
  Attempting uninstall: cython
    Found existing installation: Cython 3.0.10
    Uninstalling Cython-3.0.10:
      Successfully uninstalled Cython-3.0.10


In [ ]:
embeddings_movies = df['full_embeddings'].tolist()

In [ ]:
import umap
import hdbscan
import numpy as np

# embeddings - np.array
umap_embeddings_5dim = umap.UMAP(n_neighbors=30,
                            n_components=5,
                            min_dist=0.0,metric='cosine').fit_transform(embeddings_movies)

umap_embeddings_2dim = umap.UMAP(n_neighbors=30,
                            n_components=2,
                            min_dist=0.0,metric='cosine').fit_transform(embeddings_movies)

In [ ]:
cluster_movies = hdbscan.HDBSCAN(min_cluster_size=30,
                          metric='euclidean',
                          cluster_selection_method='eom').fit(umap_embeddings_5dim)

print (set(cluster_movies.labels_))
print (len(set(cluster_movies.labels_)))

{0, 1, 2, 3, 4, 5, 6, -1}
8


In [ ]:
from collections import Counter
Counter(cluster_movies.labels_)

Counter({-1: 1822, 5: 69, 3: 159, 1: 148, 6: 582, 4: 568, 0: 36, 2: 99})

In [ ]:
df["umap_embeddings_5dim"]  = umap_embeddings_5dim.tolist()
df["umap_embeddings_2dim"]  = umap_embeddings_2dim.tolist()
df["cluster labels"]  = cluster_movies.labels_
df.head()

Unnamed: 0                        Movie Name  \
0           0                       White Noise   
1           1                      Coach Carter   
2           2                           Elektra   
3           3                    Racing Stripes   
4           4  Tom and Jerry: Blast Off to Mars   

                                           Wiki link  \
0  https://en.wikipedia.org/wiki/White_Noise_(200...   
1         https://en.wikipedia.org/wiki/Coach_Carter   
2  https://en.wikipedia.org/wiki/Elektra_(2005_film)   
3       https://en.wikipedia.org/wiki/Racing_Stripes   
4  https://en.wikipedia.org/wiki/Tom_and_Jerry:_B...   

                                                Plot  \
0  Jonathan Rivers is an architect, married to hi...   
1  In Richmond, California, Ken Carter becomes th...   
2  After being killed,[a] Elektra Natchios is rev...   
3  During a thunderstorm, a traveling circus, Cir...   
4  Tom chases Jerry as usual from their house and...   

                                     full_embeddings  \
0  [-0.03315874934196472, 0.07238175719976425, 0....   
1  [-0.05740576982498169, 0.04432478919625282, 0....   
2  [-0.048524562269449234, 0.022518325597047806, ...   
3  [-0.02799609676003456, 0.053856637328863144, -...   
4  [0.036791738122701645, 0.08663170784711838, 0....   

                                umap_embeddings_5dim  \
0  [14.707904815673828, 20.127338409423828, 5.899...   
1  [14.488104820251465, 20.527385711669922, 6.085...   
2  [15.586479187011719, 19.64365005493164, 4.8037...   
3  [15.103070259094238, 18.968984603881836, 5.382...   
4  [15.345754623413086, 19.23481559753418, 6.1476...   

                       umap_embeddings_2dim  cluster labels  
0  [16.062963485717773, 10.282861709594727]              -1  
1   [17.547544479370117, 9.533123016357422]               5  
2      [12.891845703125, 8.414383888244629]               3  
3   [13.238007545471191, 9.083783149719238]               1  
4     [16.627107620239258, 9.4441499710083]              -1

In [ ]:
all_plots = df['Plot'].tolist()

In [ ]:
!python3 -m spacy download en_core_web_md

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.8/42.8 MB 9.8 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_md')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


In [ ]:
import spacy
nlp = spacy.load('en_core_web_md')
import tqdm.notebook as tq
all_plots_names_removed=[]
for p in tq.tqdm(all_plots):
      # Remove the tokens that you don't want.
      d = nlp(p)
      plot_annotated = [tok.text for tok in d if not
                                  (tok.is_punct or tok.is_stop
                                    or tok.is_space or tok.pos_ == "PROPN" )
                                  ]
      # plot_annotated = [tok.text for tok in d if (tok.pos_ == "NOUN" or tok.pos_ == "VERB") ]

      plot_annotated_string = ' '.join(plot_annotated)
      all_plots_names_removed.append(plot_annotated_string)

  0%|          | 0/3483 [00:00<?, ?it/s]

In [ ]:
df['filteredplot']=all_plots_names_removed
df.head()

Unnamed: 0                        Movie Name  \
0           0                       White Noise   
1           1                      Coach Carter   
2           2                           Elektra   
3           3                    Racing Stripes   
4           4  Tom and Jerry: Blast Off to Mars   

                                           Wiki link  \
0  https://en.wikipedia.org/wiki/White_Noise_(200...   
1         https://en.wikipedia.org/wiki/Coach_Carter   
2  https://en.wikipedia.org/wiki/Elektra_(2005_film)   
3       https://en.wikipedia.org/wiki/Racing_Stripes   
4  https://en.wikipedia.org/wiki/Tom_and_Jerry:_B...   

                                                Plot  \
0  Jonathan Rivers is an architect, married to hi...   
1  In Richmond, California, Ken Carter becomes th...   
2  After being killed,[a] Elektra Natchios is rev...   
3  During a thunderstorm, a traveling circus, Cir...   
4  Tom chases Jerry as usual from their house and...   

                                     full_embeddings  \
0  [-0.03315874934196472, 0.07238175719976425, 0....   
1  [-0.05740576982498169, 0.04432478919625282, 0....   
2  [-0.048524562269449234, 0.022518325597047806, ...   
3  [-0.02799609676003456, 0.053856637328863144, -...   
4  [0.036791738122701645, 0.08663170784711838, 0....   

                                umap_embeddings_5dim  \
0  [14.707904815673828, 20.127338409423828, 5.899...   
1  [14.488104820251465, 20.527385711669922, 6.085...   
2  [15.586479187011719, 19.64365005493164, 4.8037...   
3  [15.103070259094238, 18.968984603881836, 5.382...   
4  [15.345754623413086, 19.23481559753418, 6.1476...   

                       umap_embeddings_2dim  cluster labels  \
0  [16.062963485717773, 10.282861709594727]              -1   
1   [17.547544479370117, 9.533123016357422]               5   
2      [12.891845703125, 8.414383888244629]               3   
3   [13.238007545471191, 9.083783149719238]               1   
4     [16.627107620239258, 9.4441499710083]              -1   

                                        filteredplot  
0  architect married wife best selling author cou...  
1  coach basketball team played team initially un...  
2  revived blind martial arts master teaches anci...  
3  thunderstorm traveling circus accidentally lea...  
4  chases usual house town arrive astronauts head...

In [ ]:
docs_df_movies = pd.DataFrame(df, columns=["filteredplot"])
docs_df_movies['Topic'] = cluster_movies.labels_
docs_df_movies = docs_df_movies.groupby(['Topic'], as_index = False).agg({'filteredplot': ' '.join})

docs_df_movies.head()

Topic                                       filteredplot
0     -1  architect married wife best selling author cou...
1      0  restless disenchanted filmmaking enters music ...
2      1  thunderstorm traveling circus accidentally lea...
3      2  6 months film short film cursed videotape circ...
4      3  revived blind martial arts master teaches anci...

In [ ]:
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer

def c_tf_idf(documents, m, ngram_range=(1, 1)):
    count = CountVectorizer(ngram_range=ngram_range, stop_words="english").fit(documents)
    t = count.transform(documents).toarray()
    w = t.sum(axis=1)
    tf = np.divide(t.T, w)
    sum_t = t.sum(axis=0)
    idf = np.log(np.divide(m, sum_t)).reshape(-1, 1)
    tf_idf = np.multiply(tf, idf)

    return tf_idf, count

def extract_top_n_words_per_topic(tf_idf, count, docs_per_topic, n=20):
    words = count.get_feature_names_out()
    labels = list(docs_per_topic.Topic)
    tf_idf_transposed = tf_idf.T
    indices = tf_idf_transposed.argsort()[:, -n:]
    top_n_words = {label: [(words[j], tf_idf_transposed[i][j]) for j in indices[i]][::-1] for i, label in enumerate(labels)}
    return top_n_words

def extract_topic_sizes(df):
    topic_sizes = (df.groupby(['Topic'])
                     .text
                     .count()
                     .reset_index()
                     .rename({"Topic": "Topic", "text": "Size"}, axis='columns')
                     .sort_values("Size", ascending=False))
    return topic_sizes

In [ ]:
tf_idf_plots, count_plots = c_tf_idf(docs_df_movies.filteredplot.values, m=len(docs_df_movies))

In [ ]:
top_n_words_plots = extract_top_n_words_per_topic(tf_idf_plots, count_plots, docs_df_movies, n=20)

In [ ]:
from pprint import pprint


def get_topic_index_description(top_n_words,ncount):
  topic_indexes = set(top_n_words.keys())
  topic_index_description = {}
  for topic_index in topic_indexes:
    desc = top_n_words[topic_index]
    desc = desc[:ncount]
    desc_string = [x[0] for x in desc]
    desc_string_mod = " | ".join(desc_string)
    topic_index_description[topic_index]  = desc_string_mod
  return topic_index_description

topic_index_description = get_topic_index_description(top_n_words_plots,8)



pprint (topic_index_description)

{-1: 'ovens | crooks | tachyonic | powdered | tacked | healings | '
     'pickpocketing | crook',
 0: 'secessionists | andrés | piragüero | 144 | ofrenda | calves | 1492 | '
    'garment',
 1: 'roaches | koalas | clarance | unicorns | lowborn | iguana | walkman | '
    'shere',
 2: 'reefer | enfleurage | putt | perfumer | darknet | mangrove | scrubbed | '
    '606',
 3: 'etain | gong | ra | imp | hyperion | faeries | therru | elven',
 4: 'paragliding | motorhome | kilograms | superstation | blubonium | cubes | '
    'accords | guerrillas',
 5: 'serververse | presentment | fumble | benchwarmers | preseason | baseman | '
    'touchdowns | buzzer',
 6: 'rellian | forsake | classics | lately | invitational | pc | pies | feeder'}


In [ ]:
topics_companies_desc = [topic_index_description[i] for i in df["cluster labels"]]
df["topic description"]  = topics_companies_desc

df.head()

Unnamed: 0                        Movie Name  \
0           0                       White Noise   
1           1                      Coach Carter   
2           2                           Elektra   
3           3                    Racing Stripes   
4           4  Tom and Jerry: Blast Off to Mars   

                                           Wiki link  \
0  https://en.wikipedia.org/wiki/White_Noise_(200...   
1         https://en.wikipedia.org/wiki/Coach_Carter   
2  https://en.wikipedia.org/wiki/Elektra_(2005_film)   
3       https://en.wikipedia.org/wiki/Racing_Stripes   
4  https://en.wikipedia.org/wiki/Tom_and_Jerry:_B...   

                                                Plot  \
0  Jonathan Rivers is an architect, married to hi...   
1  In Richmond, California, Ken Carter becomes th...   
2  After being killed,[a] Elektra Natchios is rev...   
3  During a thunderstorm, a traveling circus, Cir...   
4  Tom chases Jerry as usual from their house and...   

                                     full_embeddings  \
0  [-0.03315874934196472, 0.07238175719976425, 0....   
1  [-0.05740576982498169, 0.04432478919625282, 0....   
2  [-0.048524562269449234, 0.022518325597047806, ...   
3  [-0.02799609676003456, 0.053856637328863144, -...   
4  [0.036791738122701645, 0.08663170784711838, 0....   

                                umap_embeddings_5dim  \
0  [14.707904815673828, 20.127338409423828, 5.899...   
1  [14.488104820251465, 20.527385711669922, 6.085...   
2  [15.586479187011719, 19.64365005493164, 4.8037...   
3  [15.103070259094238, 18.968984603881836, 5.382...   
4  [15.345754623413086, 19.23481559753418, 6.1476...   

                       umap_embeddings_2dim  cluster labels  \
0  [16.062963485717773, 10.282861709594727]              -1   
1   [17.547544479370117, 9.533123016357422]               5   
2      [12.891845703125, 8.414383888244629]               3   
3   [13.238007545471191, 9.083783149719238]               1   
4     [16.627107620239258, 9.4441499710083]              -1   

                                        filteredplot  \
0  architect married wife best selling author cou...   
1  coach basketball team played team initially un...   
2  revived blind martial arts master teaches anci...   
3  thunderstorm traveling circus accidentally lea...   
4  chases usual house town arrive astronauts head...   

                                   topic description  
0  ovens | crooks | tachyonic | powdered | tacked...  
1  serververse | presentment | fumble | benchwarm...  
2  etain | gong | ra | imp | hyperion | faeries |...  
3  roaches | koalas | clarance | unicorns | lowbo...  
4  ovens | crooks | tachyonic | powdered | tacked...

In [ ]:
import numpy as np
import plotly.express as px
# plotvalues = [[x1,x2,x3,..xn][y1,y2,y3,.....yn]]
col="umap_embeddings_2dim"
color = "topic description"
hover_data =["Movie Name"]
hover_name = "Movie Name"
plot_values = np.stack(df[col], axis=1)


x, y = plot_values[0], plot_values[1]
fig = px.scatter(
            df,
            x=x,
            y=y,
            color=color,
            hover_data=hover_data,
            title="Movies",
            hover_name=hover_name,
        )

fig.show()

In [ ]:
options_to_choose = ["Action","Comedy","Asian","Romantic","Thriller","Drama","Fantasy","Mystery","Extraterrestrial","Adventure","Horror","Scifi","Superhero","Fiction","Animals","Other"]
print (options_to_choose)

['Action', 'Comedy', 'Asian', 'Romantic', 'Thriller', 'Drama', 'Fantasy', 'Mystery', 'Extraterrestrial', 'Adventure', 'Horror', 'Scifi', 'Superhero', 'Fiction', 'Animals', 'Other']


In [ ]:
import ipywidgets as widgets                        # Creating widgets
from IPython.display import display,HTML                 # Displaying widgets
# display(HTML("<style>.container { width:100% !important; }</style>"))
output = widgets.Output()
# Creating dropdown objects
dropdownobjects =[widgets.Dropdown(options = options_to_choose, description=str(key),width =75) for key in topic_index_description]

# Display the dropdowns
input_widgets = widgets.VBox(dropdownobjects)
pprint (topic_index_description)
print ("Choose from the dropdown the best replacement for a given word and proceed to the next cell : \n")
display(input_widgets)

{-1: 'ovens | crooks | tachyonic | powdered | tacked | healings | '
     'pickpocketing | crook',
 0: 'secessionists | andrés | piragüero | 144 | ofrenda | calves | 1492 | '
    'garment',
 1: 'roaches | koalas | clarance | unicorns | lowborn | iguana | walkman | '
    'shere',
 2: 'reefer | enfleurage | putt | perfumer | darknet | mangrove | scrubbed | '
    '606',
 3: 'etain | gong | ra | imp | hyperion | faeries | therru | elven',
 4: 'paragliding | motorhome | kilograms | superstation | blubonium | cubes | '
    'accords | guerrillas',
 5: 'serververse | presentment | fumble | benchwarmers | preseason | baseman | '
    'touchdowns | buzzer',
 6: 'rellian | forsake | classics | lately | invitational | pc | pies | feeder'}
Choose from the dropdown the best replacement for a given word and proceed to the next cell : 



In [ ]:
final_UI_chosen_mapping = {}
for key,choice in zip(topic_index_description.keys(),dropdownobjects):
  final_UI_chosen_mapping[key] = choice.value
pprint (final_UI_chosen_mapping)

{-1: 'Action',
 0: 'Action',
 1: 'Action',
 2: 'Action',
 3: 'Action',
 4: 'Action',
 5: 'Action',
 6: 'Action'}


In [ ]:
topics_grants_desc_short = [final_UI_chosen_mapping[i] for i in df["cluster labels"]]
df["topic final"]  = topics_grants_desc_short
df.head()

Unnamed: 0                        Movie Name  \
0           0                       White Noise   
1           1                      Coach Carter   
2           2                           Elektra   
3           3                    Racing Stripes   
4           4  Tom and Jerry: Blast Off to Mars   

                                           Wiki link  \
0  https://en.wikipedia.org/wiki/White_Noise_(200...   
1         https://en.wikipedia.org/wiki/Coach_Carter   
2  https://en.wikipedia.org/wiki/Elektra_(2005_film)   
3       https://en.wikipedia.org/wiki/Racing_Stripes   
4  https://en.wikipedia.org/wiki/Tom_and_Jerry:_B...   

                                                Plot  \
0  Jonathan Rivers is an architect, married to hi...   
1  In Richmond, California, Ken Carter becomes th...   
2  After being killed,[a] Elektra Natchios is rev...   
3  During a thunderstorm, a traveling circus, Cir...   
4  Tom chases Jerry as usual from their house and...   

                                     full_embeddings  \
0  [-0.03315874934196472, 0.07238175719976425, 0....   
1  [-0.05740576982498169, 0.04432478919625282, 0....   
2  [-0.048524562269449234, 0.022518325597047806, ...   
3  [-0.02799609676003456, 0.053856637328863144, -...   
4  [0.036791738122701645, 0.08663170784711838, 0....   

                                umap_embeddings_5dim  \
0  [14.707904815673828, 20.127338409423828, 5.899...   
1  [14.488104820251465, 20.527385711669922, 6.085...   
2  [15.586479187011719, 19.64365005493164, 4.8037...   
3  [15.103070259094238, 18.968984603881836, 5.382...   
4  [15.345754623413086, 19.23481559753418, 6.1476...   

                       umap_embeddings_2dim  cluster labels  \
0  [16.062963485717773, 10.282861709594727]              -1   
1   [17.547544479370117, 9.533123016357422]               5   
2      [12.891845703125, 8.414383888244629]               3   
3   [13.238007545471191, 9.083783149719238]               1   
4     [16.627107620239258, 9.4441499710083]              -1   

                                        filteredplot  \
0  architect married wife best selling author cou...   
1  coach basketball team played team initially un...   
2  revived blind martial arts master teaches anci...   
3  thunderstorm traveling circus accidentally lea...   
4  chases usual house town arrive astronauts head...   

                                   topic description topic final  
0  ovens | crooks | tachyonic | powdered | tacked...      Action  
1  serververse | presentment | fumble | benchwarm...      Action  
2  etain | gong | ra | imp | hyperion | faeries |...      Action  
3  roaches | koalas | clarance | unicorns | lowbo...      Action  
4  ovens | crooks | tachyonic | powdered | tacked...      Action

In [ ]:
import numpy as np
import plotly.express as px
# plotvalues = [[x1,x2,x3,..xn][y1,y2,y3,.....yn]]
col="umap_embeddings_2dim"
color = "topic final"
hover_data =["Movie Name"]
hover_name = "Movie Name"
plot_values = np.stack(df[col], axis=1)


x, y = plot_values[0], plot_values[1]
fig = px.scatter(
            df,
            x=x,
            y=y,
            color=color,
            hover_data=hover_data,
            title="Movies",
            hover_name=hover_name,
        )

fig.show()

# Build a paraphraser

In [ ]:
!pip install --upgrade openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 320.6/320.6 kB 4.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 9.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.2 MB/s eta 0:00:00
  Attempting uninstall: openai
    Found existing installation: openai 0.24.0
    Uninstalling openai-0.24.0:
      Successfully uninstalled openai-0.24.0
